In [2]:
!pip install catboost

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.2/98.2 MB 2.2 MB/s eta 0:00:00


In [16]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn import linear_model
from sklearn.metrics import r2_score, mean_absolute_error
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, CatBoostRegressor, Pool, cv, sum_models
import torch
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn import linear_model
from sklearn.ensemble import RandomForestRegressor
import numpy as np

In [18]:
df = pd.read_csv("dataset.csv")

# **Линейная регрессия**

In [5]:
X = df.drop(['price_doc'], axis=1)
y = df['price_doc']

X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, random_state=42)

In [10]:
from sklearn import linear_model
from sklearn.metrics import r2_score, mean_absolute_error

model_linear = linear_model.LinearRegression()
model_linear.fit(X_train, y_train)

train_pred = model_linear.predict(X_train)
print(f'Для тренировочной выборики {r2_score(y_train, train_pred)}')
print(f'Mae: {mean_absolute_error(y_train, train_pred)}')

test_pred = model_linear.predict(X_test)
print(f'Для тренировочной выборики {r2_score(y_test, test_pred)}')
print(f'Mae: {mean_absolute_error(y_test, test_pred)}')

Для тренировочной выборики 0.5216346123181121
Mae: 1634302.3265425148
Для тренировочной выборики 0.49718497926563054
Mae: 1708019.4300962372


Построена базовая модель линейной регрессии, также можно попробовать другие модели линейной регрессии

In [11]:
model_ridge = linear_model.Ridge(alpha=0.5)
model_ridge.fit(X_train, y_train)

train_pred = model_ridge.predict(X_train)
print(f'Для тренировочной выборики {r2_score(y_train, train_pred)}')
print(f'Mae: {mean_absolute_error(y_train, train_pred)}')

test_pred = model_ridge.predict(X_test)
print(f'Для тренировочной выборики {r2_score(y_test, test_pred)}')
print(f'Mae: {mean_absolute_error(y_test, test_pred)}')

Для тренировочной выборики 0.5216345891530869
Mae: 1634284.1888891712
Для тренировочной выборики 0.49718969059599283
Mae: 1707984.666638899


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=7.90544e-19): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T


In [12]:
model_lasso = linear_model.Lasso(alpha=0.1)
model_lasso.fit(X_train, y_train)

train_pred = model_lasso.predict(X_train)
print(f'Для тренировочной выборики {r2_score(y_train, train_pred)}')
print(f'Mae: {mean_absolute_error(y_train, train_pred)}')

test_pred = model_lasso.predict(X_test)
print(f'Для тренировочной выборики {r2_score(y_test, test_pred)}')
print(f'Mae: {mean_absolute_error(y_test, test_pred)}')

Для тренировочной выборики 0.5216346123179196
Mae: 1634302.2509084677
Для тренировочной выборики 0.4971849954757549
Mae: 1708019.3312681126


In [13]:
model_bayes = linear_model.BayesianRidge()
model_bayes.fit(X_train, y_train)

train_pred = model_bayes.predict(X_train)
print(f'Для тренировочной выборики {r2_score(y_train, train_pred)}')
print(f'Mae: {mean_absolute_error(y_train, train_pred)}')

test_pred = model_bayes.predict(X_test)
print(f'Для тренировочной выборики {r2_score(y_test, test_pred)}')
print(f'Mae: {mean_absolute_error(y_test, test_pred)}')

Для тренировочной выборики 0.5209705299444245
Mae: 1632345.1820065735
Для тренировочной выборики 0.4974111340365659
Mae: 1704082.864188431


# **CatBoost**

In [19]:
df_catboost = df.copy()
float_cols = df_catboost.select_dtypes(include=['float64']).columns
# Преобразуем эти столбцы к целочисленному типу
df_catboost[float_cols] = df_catboost[float_cols].applymap(np.int64)
df_catboost.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15266 entries, 0 to 15265
Data columns (total 80 columns):
 #   Column                                 Non-Null Count  Dtype
---  ------                                 --------------  -----
 0   Unnamed: 0                             15266 non-null  int64
 1   full_sq                                15266 non-null  int64
 2   life_sq                                15266 non-null  int64
 3   floor                                  15266 non-null  int64
 4   max_floor                              15266 non-null  int64
 5   material                               15266 non-null  int64
 6   build_year                             15266 non-null  int64
 7   kitch_sq                               15266 non-null  int64
 8   state                                  15266 non-null  int64
 9   area_m                                 15266 non-null  int64
 10  raion_popul                            15266 non-null  int64
 11  green_zone_part             

In [32]:
X = df_catboost.drop(['price_doc'], axis=1)
y = df_catboost['price_doc']

X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, random_state=42)

In [20]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = '0'

In [21]:
import catboost
print(catboost.__version__)

1.2.5


In [24]:
cat_features = [i for i in range(78)]
train_dataset = Pool(data=X_train,
                     label=y_train,
                     cat_features=cat_features)

eval_dataset = Pool(data=X_test,
                    label=y_test,
                    cat_features=cat_features)

model = CatBoostRegressor(iterations=20000,
                           grow_policy="Depthwise",
                           loss_function = 'RMSE',
                           eval_metric = 'R2',
                           early_stopping_rounds = 1000,
                           verbose = False,
                           use_best_model=True
                         )

model.fit(train_dataset, eval_set=eval_dataset, logging_level='Silent', plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [25]:
model.best_iteration_

7876

In [26]:
Y_hat_train = [yhat for yhat in model.predict(X_train)]
Y_hat = [yhat for yhat in model.predict(X_test)]

from sklearn.metrics import r2_score
print(r2_score(y_train, Y_hat_train))
print(r2_score(y_test, Y_hat))

0.7293166604090213
0.5765036757820499


In [27]:
!pip install lightgbm

In [28]:
from lightgbm import LGBMRegressor

In [34]:
model = LGBMRegressor(max_depth=101,
                             min_child_samples=20,
                             num_leaves=11,
                             n_estimators=300,
                             random_state=47,
                      force_row_wise=True)

In [36]:
import re
df = df.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))

In [37]:
X = df.drop(['price_doc'], axis=1)
y = df['price_doc']

X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, random_state=42)

In [38]:
model.fit(X_train, y_train)

[LightGBM] [Info] Total Bins 5405
[LightGBM] [Info] Number of data points in the train set: 12212, number of used features: 46
[LightGBM] [Info] Start training from score 7390646.049787


LGBMRegressor(force_row_wise=True, max_depth=101, n_estimators=300,
              num_leaves=11, random_state=47)

In [39]:
train_pred = model.predict(X_train)
print(f'Для тренировочной выборики {r2_score(y_train, train_pred)}')
print(f'Mae: {mean_absolute_error(y_train, train_pred)}')

test_pred = model.predict(X_test)
print(f'Для тренировочной выборики {r2_score(y_test, test_pred)}')
print(f'Mae: {mean_absolute_error(y_test, test_pred)}')

Для тренировочной выборики 0.7404465531054465
Mae: 1144337.8195078445
Для тренировочной выборики 0.5956807208672782
Mae: 1435287.781635658


# **Метод случайного леса**

In [ ]:
from google.colab import output
output.enable_custom_widget_manager()

Support for third party widgets will remain active for the duration of the session. To disable support:

In [ ]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV

X_train, X_test, y_train, y_test = train_test_split(X, y,
                                              train_size=0.8, random_state=42)


parametrs = {'n_estimators': range(300, 301, 1),
              'max_depth': range (5,26, 10),
              'min_samples_leaf': range (1,11, 5),
}

clf = RandomForestRegressor()

grid = GridSearchCV(clf, parametrs, cv=5)
grid.fit(X_train, y_train)

GridSearchCV(cv=5, estimator=RandomForestRegressor(),
             param_grid={'max_depth': range(5, 26, 10),
                         'min_samples_leaf': range(1, 11, 5),
                         'n_estimators': range(300, 301)})

In [ ]:
grid.best_params_

{'max_depth': 25, 'min_samples_leaf': 6, 'n_estimators': 300}

In [ ]:
tree = RandomForestRegressor(
    n_estimators=300,
    max_depth=25,
    min_samples_leaf=6,
    n_jobs= -1,
    random_state=42
)

# инициализация модели
tree.fit(X_train, y_train)

#обучение модели
test_pred = tree.predict(X_test)
train_pred = tree.predict(X_train)

print(f'Для тренировочной выборики {r2_score(y_train, train_pred)}')
print(f'Mae: {mean_absolute_error(y_train, train_pred)}')

print(f'Для тренировочной выборики {r2_score(y_test, test_pred)}')
print(f'Mae: {mean_absolute_error(y_test, test_pred)}')

Для тренировочной выборики 0.7916005283209813
Mae: 993655.9759478474
Для тренировочной выборики 0.5709203945030253
Mae: 1475213.8437723126


На основе проведенных эксперементов можно выделить оптимальную модель для прогнозирования цен на недвижимость